# Overview:

In this notebook, you will see demo of how [Redshift Serverelss AI Driven](https://aws.amazon.com/about-aws/whats-new/2023/11/amazon-redshift-serverless-ai-driven-scaling-optimizations-preview/) feature will intelligently predict your workload compute needs and scale pro-actively.

We will demonstrate this feature in following three scenarios.

- Use Case #1 - A complex query which usually runs for long time (~25minutes) with default compute
- Use Case #2 - Sudden spike in ingestion volume (3x increase - 720 million to 2.1 billion). 
- Use Case #3 - Spectrum query scanning large datasets (~TBs).

# Pre-requisites

1. Create Redshift Serverelss workgroup in preview mode.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-workgroup-preview.html) to create preview wokrgroup.
2. While creating preview group, choose **Performance and Cost Controls**-->**Price-performance target**, and adjust the slider to **Optimized for performance**.  Reference [blog](https://aws.amazon.com/blogs/aws/amazon-redshift-adds-new-ai-capabilities-to-boost-efficiency-and-productivity/)
3. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

## Setup Test Data

As first step, let us screate TPC-DS tables.  You will use [TPC-DS 1TB](https://github.com/awslabs/amazon-redshift-utils/blob/master/src/CloudDataWarehouseBenchmark/Cloud-DWB-Derived-from-TPCDS/1TB/ddl.sql)  Cloud DataWarehouse benchmark data for demonstrating this feature.

In [0]:
-- Run below scripts to create tables

create table date_dim
(
    d_date_sk                 integer               not null,
    d_date_id                 char(16)              not null,
    d_date                    date,
    d_month_seq               integer                       ,
    d_week_seq                integer                       ,
    d_quarter_seq             integer                       ,
    d_year                    integer                       ,
    d_dow                     integer                       ,
    d_moy                     integer                       ,
    d_dom                     integer                       ,
    d_qoy                     integer                       ,
    d_fy_year                 integer                       ,
    d_fy_quarter_seq          integer                       ,
    d_fy_week_seq             integer                       ,
    d_day_name                char(9)                       ,
    d_quarter_name            char(6)                       ,
    d_holiday                 char(1)                       ,
    d_weekend                 char(1)                       ,
    d_following_holiday       char(1)                       ,
    d_first_dom               integer                       ,
    d_last_dom                integer                       ,
    d_same_day_ly             integer                       ,
    d_same_day_lq             integer                       ,
    d_current_day             char(1)                       ,
    d_current_week            char(1)                       ,
    d_current_month           char(1)                       ,
    d_current_quarter         char(1)                       ,
    d_current_year            char(1)                       ,
    primary key (d_date_sk)
) diststyle all;

create table web_sales
(
 ws_sold_date_sk int4 ,             
  ws_sold_time_sk int4 ,        
  ws_ship_date_sk int4 ,        
  ws_item_sk int4 not null ,    
  ws_bill_customer_sk int4 ,    
  ws_bill_cdemo_sk int4 ,       
  ws_bill_hdemo_sk int4 ,       
  ws_bill_addr_sk int4 ,        
  ws_ship_customer_sk int4 ,    
  ws_ship_cdemo_sk int4 ,       
  ws_ship_hdemo_sk int4 ,       
  ws_ship_addr_sk int4 ,        
  ws_web_page_sk int4 ,         
  ws_web_site_sk int4 ,         
  ws_ship_mode_sk int4 ,        
  ws_warehouse_sk int4 ,        
  ws_promo_sk int4 ,            
  ws_order_number int8 not null,
  ws_quantity int4 ,            
  ws_wholesale_cost numeric(7,2) ,                
  ws_list_price numeric(7,2) ,  
  ws_sales_price numeric(7,2) , 
  ws_ext_discount_amt numeric(7,2) ,              
  ws_ext_sales_price numeric(7,2) ,
  ws_ext_wholesale_cost numeric(7,2) ,               
  ws_ext_list_price numeric(7,2) , 
  ws_ext_tax numeric(7,2) ,     
  ws_coupon_amt numeric(7,2) ,  
  ws_ext_ship_cost numeric(7,2) ,                 
  ws_net_paid numeric(7,2) ,    
  ws_net_paid_inc_tax numeric(7,2) ,              
  ws_net_paid_inc_ship numeric(7,2) ,             
  ws_net_paid_inc_ship_tax numeric(7,2) ,         
  ws_net_profit numeric(7,2)                      
  ,primary key (ws_item_sk, ws_order_number)
) distkey(ws_order_number) sortkey(ws_sold_date_sk);

create table catalog_sales
(
 cs_sold_date_sk int4 ,          
  cs_sold_time_sk int4 ,        
  cs_ship_date_sk int4 ,        
  cs_bill_customer_sk int4 ,    
  cs_bill_cdemo_sk int4 ,       
  cs_bill_hdemo_sk int4 ,       
  cs_bill_addr_sk int4 ,        
  cs_ship_customer_sk int4 ,    
  cs_ship_cdemo_sk int4 ,       
  cs_ship_hdemo_sk int4 ,       
  cs_ship_addr_sk int4 ,        
  cs_call_center_sk int4 ,      
  cs_catalog_page_sk int4 ,     
  cs_ship_mode_sk int4 ,        
  cs_warehouse_sk int4 ,        
  cs_item_sk int4 not null ,    
  cs_promo_sk int4 ,            
  cs_order_number int8 not null ,                 
  cs_quantity int4 ,            
  cs_wholesale_cost numeric(7,2) ,                
  cs_list_price numeric(7,2) ,  
  cs_sales_price numeric(7,2) , 
  cs_ext_discount_amt numeric(7,2) ,              
  cs_ext_sales_price numeric(7,2) ,               
  cs_ext_wholesale_cost numeric(7,2) ,            
  cs_ext_list_price numeric(7,2) ,
  cs_ext_tax numeric(7,2) ,     
  cs_coupon_amt numeric(7,2) , 
  cs_ext_ship_cost numeric(7,2) ,                
  cs_net_paid numeric(7,2) ,   
  cs_net_paid_inc_tax numeric(7,2) ,             
  cs_net_paid_inc_ship numeric(7,2) ,            
  cs_net_paid_inc_ship_tax numeric(7,2) ,        
  cs_net_profit numeric(7,2)                     
  ,primary key (cs_item_sk, cs_order_number)
) distkey(cs_item_sk) sortkey(cs_sold_date_sk);

create table store_sales
(
ss_sold_date_sk int4 ,            
  ss_sold_time_sk int4 ,     
  ss_item_sk int4 not null ,      
  ss_customer_sk int4 ,           
  ss_cdemo_sk int4 ,              
  ss_hdemo_sk int4 ,         
  ss_addr_sk int4 ,               
  ss_store_sk int4 ,           
  ss_promo_sk int4 ,           
  ss_ticket_number int8 not null,        
  ss_quantity int4 ,           
  ss_wholesale_cost numeric(7,2) ,          
  ss_list_price numeric(7,2) ,              
  ss_sales_price numeric(7,2) ,
  ss_ext_discount_amt numeric(7,2) ,             
  ss_ext_sales_price numeric(7,2) ,              
  ss_ext_wholesale_cost numeric(7,2) ,           
  ss_ext_list_price numeric(7,2) ,               
  ss_ext_tax numeric(7,2) ,                 
  ss_coupon_amt numeric(7,2) , 
  ss_net_paid numeric(7,2) ,   
  ss_net_paid_inc_tax numeric(7,2) ,             
  ss_net_profit numeric(7,2)                     
  ,primary key (ss_item_sk, ss_ticket_number)
) distkey(ss_item_sk) sortkey(ss_sold_date_sk);

create table store_returns
(
sr_returned_date_sk int4 ,    
  sr_return_time_sk int4 ,    
  sr_item_sk int4 not null ,  
  sr_customer_sk int4 ,       
  sr_cdemo_sk int4 ,          
  sr_hdemo_sk int4 ,          
  sr_addr_sk int4 ,           
  sr_store_sk int4 ,          
  sr_reason_sk int4 ,         
  sr_ticket_number int8 not null,               
  sr_return_quantity int4 ,   
  sr_return_amt numeric(7,2) ,
  sr_return_tax numeric(7,2) ,
  sr_return_amt_inc_tax numeric(7,2) ,          
  sr_fee numeric(7,2) ,       
  sr_return_ship_cost numeric(7,2) ,            
  sr_refunded_cash numeric(7,2) ,               
  sr_reversed_charge numeric(7,2) ,             
  sr_store_credit numeric(7,2) ,                
  sr_net_loss numeric(7,2)                      
  ,primary key (sr_item_sk, sr_ticket_number)
) distkey(sr_item_sk) sortkey(sr_returned_date_sk);

create table catalog_returns
(
 cr_returned_date_sk int4 ,  
  cr_returned_time_sk int4 , 
  cr_item_sk int4 not null , 
  cr_refunded_customer_sk int4 ,
  cr_refunded_cdemo_sk int4 ,   
  cr_refunded_hdemo_sk int4 ,   
  cr_refunded_addr_sk int4 ,    
  cr_returning_customer_sk int4 ,
  cr_returning_cdemo_sk int4 ,   
  cr_returning_hdemo_sk int4 ,  
  cr_returning_addr_sk int4 ,   
  cr_call_center_sk int4 ,      
  cr_catalog_page_sk int4 ,     
  cr_ship_mode_sk int4 ,        
  cr_warehouse_sk int4 ,        
  cr_reason_sk int4 ,           
  cr_order_number int8 not null,
  cr_return_quantity int4 ,     
  cr_return_amount numeric(7,2) ,
  cr_return_tax numeric(7,2) ,   
  cr_return_amt_inc_tax numeric(7,2) ,
  cr_fee numeric(7,2) ,         
  cr_return_ship_cost numeric(7,2) , 
  cr_refunded_cash numeric(7,2) ,    
  cr_reversed_charge numeric(7,2) ,  
  cr_store_credit numeric(7,2) ,
  cr_net_loss numeric(7,2)      
  ,primary key (cr_item_sk, cr_order_number)
) distkey(cr_item_sk) sortkey(cr_returned_date_sk);

create table web_returns
(
wr_returned_date_sk int4 ,   
  wr_returned_time_sk int4 , 
  wr_item_sk int4 not null , 
  wr_refunded_customer_sk int4 ,
  wr_refunded_cdemo_sk int4 ,   
  wr_refunded_hdemo_sk int4 ,   
  wr_refunded_addr_sk int4 ,    
  wr_returning_customer_sk int4 ,
  wr_returning_cdemo_sk int4 ,   
  wr_returning_hdemo_sk int4 ,  
  wr_returning_addr_sk int4 ,   
  wr_web_page_sk int4 ,         
  wr_reason_sk int4 ,           
  wr_order_number int8 not null,
  wr_return_quantity int4 ,     
  wr_return_amt numeric(7,2) ,  
  wr_return_tax numeric(7,2) ,  
  wr_return_amt_inc_tax numeric(7,2) ,
  wr_fee numeric(7,2) ,         
  wr_return_ship_cost numeric(7,2) ,
  wr_refunded_cash numeric(7,2) ,   
  wr_reversed_charge numeric(7,2) ,  
  wr_account_credit numeric(7,2) ,   
  wr_net_loss numeric(7,2)           
  ,primary key (wr_item_sk, wr_order_number)
) distkey(wr_order_number) sortkey(wr_returned_date_sk);

Load Test data and validate counts

In [0]:
-- Run below scripts to load the test data

-- Please ensure you associated an IAM role to cluster as default role and it has S3 full access.

copy date_dim from 's3://redshift-downloads/TPC-DS/2.13/1TB/date_dim/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';

copy web_sales from 's3://redshift-downloads/TPC-DS/2.13/1TB/web_sales/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy web_returns from 's3://redshift-downloads/TPC-DS/2.13/1TB/web_returns/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';

copy store_sales from 's3://redshift-downloads/TPC-DS/2.13/1TB/store_sales/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy store_returns from 's3://redshift-downloads/TPC-DS/2.13/1TB/store_returns/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';

copy catalog_sales from 's3://redshift-downloads/TPC-DS/2.13/1TB/catalog_sales/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
copy catalog_returns from 's3://redshift-downloads/TPC-DS/2.13/1TB/catalog_returns/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';



select count(*) from date_dim;  -- 73049 
select count(*) from web_sales;  -- 720000376 
select count(*) from web_returns;  -- 71997522  
select count(*) from store_sales;  -- 2879987999 
select count(*) from store_returns;  -- 287999764 
select count(*) from catalog_sales;  -- 1439980416
select count(*) from catalog_returns;  -- 143996756

# Use Case #1
Proactively predict run times of complex/long running queries and scale ahead to finish faster.  With AI drive scaling, Redshift servereless need not wait for cumulative queuing to scale compute.  It scales based on predicting run times and the best part is it scales for even single query unlinke earlier scaling queuing based scaling approach.

NOTE: For the very first run of this query, the data warehouse will not have history of the query statistics. So you may need to run this query twice for scaling algorithms to make scaling decisions. Please re-run if the query did not scale on the very first run.

In [0]:
-- The following queries usually runs for 25 minutes with default Serverelss configuration. With AI driven scalaing, Redshift serverelss automatically scales ahead and runs the query much faster balancing the price and performance.



SET enable_result_cache_for_session TO off;
with /* TPC-DS demo query */
	ws as
	(select d_year AS ws_sold_year, ws_item_sk,    ws_bill_customer_sk
     ws_customer_sk,    sum(ws_quantity) ws_qty,    sum(ws_wholesale_cost) ws_wc,
        sum(ws_sales_price) ws_sp   from web_sales   left join web_returns on
     wr_order_number=ws_order_number and ws_item_sk=wr_item_sk   join date_dim
     on ws_sold_date_sk = d_date_sk   where wr_order_number is null   group by
     d_year, ws_item_sk, ws_bill_customer_sk   ),
	cs as  
	(select d_year AS cs_sold_year,
     cs_item_sk,    cs_bill_customer_sk cs_customer_sk,    sum(cs_quantity) cs_qty,
        sum(cs_wholesale_cost) cs_wc,    sum(cs_sales_price) cs_sp   from catalog_sales
       left join catalog_returns on cr_order_number=cs_order_number and cs_item_sk=cr_item_sk
       join date_dim on cs_sold_date_sk = d_date_sk   where cr_order_number is
     null   group by d_year, cs_item_sk, cs_bill_customer_sk   ),
	ss as  
	(select
     d_year AS ss_sold_year, ss_item_sk,    ss_customer_sk,    sum(ss_quantity)
     ss_qty,    sum(ss_wholesale_cost) ss_wc,    sum(ss_sales_price) ss_sp
       from store_sales left join store_returns on sr_ticket_number=ss_ticket_number
     and ss_item_sk=sr_item_sk   join date_dim on ss_sold_date_sk = d_date_sk
       where sr_ticket_number is null   group by d_year, ss_item_sk, ss_customer_sk
       ) 
	   
	   select 
	   ss_customer_sk,round(ss_qty/(coalesce(ws_qty+cs_qty,1)),2)
     ratio,ss_qty store_qty, ss_wc store_wholesale_cost, ss_sp store_sales_price,
    coalesce(ws_qty,0)+coalesce(cs_qty,0) other_chan_qty,coalesce(ws_wc,0)+coalesce(cs_wc,0)
     other_chan_wholesale_cost,coalesce(ws_sp,0)+coalesce(cs_sp,0) other_chan_sales_price
    from ss left join ws on (ws_sold_year=ss_sold_year and ws_item_sk=ss_item_sk
     and ws_customer_sk=ss_customer_sk)left join cs on (cs_sold_year=ss_sold_year
     and cs_item_sk=cs_item_sk and cs_customer_sk=ss_customer_sk)where coalesce(ws_qty,0)>0
     and coalesce(cs_qty, 0)>0 order by   ss_customer_sk,  ss_qty desc, ss_wc
     desc, ss_sp desc,  other_chan_qty,  other_chan_wholesale_cost,  other_chan_sales_price,
      round(ss_qty/(coalesce(ws_qty+cs_qty,1)),2);

### Review the compute used and the approximate cost of the query

In [0]:
-- Review total elapsed time of the query.  It should be much lower than ~25minutes.
select query_id,query_text,start_time,end_time, elapsed_time/1000000.0 duration_in_seconds 
from sys_query_history 
where query_text like '%TPC-DS demo query%'
and query_text not like '%sys_query_history%'
order by start_time desc

In [0]:
-- Observe the compute scaled during the above start_time and end_time period.  Replace start_time and end_time in below query from output of the above query
select * from sys_serverless_usage
where end_time >= '2024-06-03 00:17:12.322353' 
and end_time <= DATEADD(minute,1,'2024-06-03 00:19:11.553218') 
order by end_time asc

-- Example
--select * from sys_serverless_usage
--where end_time >= '2023-12-29 21:32:33.849344' 
--and end_time <= DATEADD(minute,1,'2023-12-29 21:33:41.304871') 
--order by end_time asc

## Show scaling activity on the console 
1. Navigate to ***Resource monitoring*** under ***Monitoring**.
2. The default workgroup will be selected by default, but you can choose the workgroup you would like to monitor.
3. In the Metric filters section, expand Additional filtering options.  
4. Choose a 1-minute time interval (for example) and review the results.
5. Please ensure you select timestamps in the range of above query run time.

Please refer this [blog](https://aws-preview.aka.amazon.com/blogs/big-data/configure-monitoring-limits-and-alarms-in-amazon-redshift-serverless-to-keep-costs-predictable/) if you need more guidance.

# Use Case #2
Let us say your daily ingestion job process 720 million records and completes in an average 2minutes.  Due to some event (e.g month end processing), your volumes increased by 3X and now your ingestion job needs to process 2.1 billion records.  

In existing scaling approach, this will increase your ingestion job run time unless cumulative queue time is greater than ~60 seconds at instance level.  But with AI driven scaling, in performance optimized mode, Redshift automatically scales compute to complete your ingestion job within regular runtimes.  It helps to protect your ingest job SLAs.

In [0]:
-- You ran below copy job to ingest 720 million records in to web_sales table.  
-- copy web_sales from 's3://redshift-downloads/TPC-DS/2.13/1TB/web_sales/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';
--Let us see the copy job run metrics

select query_id,table_name,data_source,loaded_rows,duration/1000000.0 duration_in_seconds , start_time,end_time
from sys_load_history 
where 
table_name='web_sales'
order by start_time desc

In [0]:
-- Now let us run same ingestion job with 2.1 billion records

copy web_sales from 's3://redshift-downloads/TPC-DS/2.13/3TB/web_sales/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';

In [0]:
--Let us see the copy job run metrics again.  The first row is for the latest run and you can also identify by the loaded_rows value

select query_id,table_name,data_source,loaded_rows,duration/1000000.0 duration_in_seconds , start_time,end_time
from sys_load_history 
where 
table_name='web_sales'
order by start_time desc

In [0]:
-- Observe the compute scaled during the above start_time and end_time period.  Replace start_time and end_time in below query from output of the above query.  
select * from sys_serverless_usage
where end_time >= '2024-06-03 00:33:18.404452' 
and end_time <= DATEADD(minute,1,'2024-06-03 00:35:24.03242') 
order by end_time asc

-- You can notice the increased compute_capacity.  It proves the Redshift automatically scaled to process 3x increase in incoming volume.

# Use case #3

In this use case, you will create external tables pointing to TPC-DS 3TB data on an S3 location and demonstrate how Redshift Serverless scales for a spectrum query scanning large volume of data.

NOTE: In below SQL, please replace ‘<ARN of the default IAM role attached>’ with the ARN of the default IAM role attached in step3 of the pre-requisites.

In [0]:
-- Create external schema
--drop  schema ext_tpcds_3t
create external schema ext_tpcds_3t
from data catalog
database ext_tpcds_db
iam_role 'arn:aws:iam::445818506882:role/RedshiftImmersionRole'
create external database if not exists;

In [0]:
-- Create External for TPC-DS 3TB dataset

CREATE EXTERNAL TABLE ext_tpcds_3t.date_dim (
    d_date_sk                 integer ,
    d_date_id                 char(16),
    d_date                    date,
    d_month_seq               integer,
    d_week_seq                integer,
    d_quarter_seq             integer,
    d_year                    integer,
    d_dow                     integer,
    d_moy                     integer,
    d_dom                     integer,
    d_qoy                     integer,
    d_fy_year                 integer,
    d_fy_quarter_seq          integer,
    d_fy_week_seq             integer,
    d_day_name                char(9),
    d_quarter_name            char(6),
    d_holiday                 char(1),
    d_weekend                 char(1),
    d_following_holiday       char(1),
    d_first_dom               integer,
    d_last_dom                integer,
    d_same_day_ly             integer,
    d_same_day_lq             integer,
    d_current_day             char(1),
    d_current_week            char(1),
    d_current_month           char(1),
    d_current_quarter         char(1),
    d_current_year            char(1)                       
    )
    row format delimited
    fields terminated by '|'
    stored as textfile
    LOCATION 's3://redshift-downloads/TPC-DS/2.13/3TB/date_dim/';



CREATE EXTERNAL TABLE ext_tpcds_3t.web_sales
(
 ws_sold_date_sk int4 ,             
  ws_sold_time_sk int4 ,        
  ws_ship_date_sk int4 ,        
  ws_item_sk int4  ,    
  ws_bill_customer_sk int4 ,    
  ws_bill_cdemo_sk int4 ,       
  ws_bill_hdemo_sk int4 ,       
  ws_bill_addr_sk int4 ,        
  ws_ship_customer_sk int4 ,    
  ws_ship_cdemo_sk int4 ,       
  ws_ship_hdemo_sk int4 ,       
  ws_ship_addr_sk int4 ,        
  ws_web_page_sk int4 ,         
  ws_web_site_sk int4 ,         
  ws_ship_mode_sk int4 ,        
  ws_warehouse_sk int4 ,        
  ws_promo_sk int4 ,            
  ws_order_number int8 ,
  ws_quantity int4 ,            
  ws_wholesale_cost numeric(7,2) ,                
  ws_list_price numeric(7,2) ,  
  ws_sales_price numeric(7,2) , 
  ws_ext_discount_amt numeric(7,2) ,              
  ws_ext_sales_price numeric(7,2) ,
  ws_ext_wholesale_cost numeric(7,2) ,               
  ws_ext_list_price numeric(7,2) , 
  ws_ext_tax numeric(7,2) ,     
  ws_coupon_amt numeric(7,2) ,  
  ws_ext_ship_cost numeric(7,2) ,                 
  ws_net_paid numeric(7,2) ,    
  ws_net_paid_inc_tax numeric(7,2) ,              
  ws_net_paid_inc_ship numeric(7,2) ,             
  ws_net_paid_inc_ship_tax numeric(7,2) ,         
  ws_net_profit numeric(7,2)
)
row format delimited
fields terminated by '|'
stored as textfile
LOCATION 's3://redshift-downloads/TPC-DS/2.13/3TB/web_sales/';


CREATE EXTERNAL TABLE ext_tpcds_3t.catalog_sales
(
 cs_sold_date_sk int4 ,          
  cs_sold_time_sk int4 ,        
  cs_ship_date_sk int4 ,        
  cs_bill_customer_sk int4 ,    
  cs_bill_cdemo_sk int4 ,       
  cs_bill_hdemo_sk int4 ,       
  cs_bill_addr_sk int4 ,        
  cs_ship_customer_sk int4 ,    
  cs_ship_cdemo_sk int4 ,       
  cs_ship_hdemo_sk int4 ,       
  cs_ship_addr_sk int4 ,        
  cs_call_center_sk int4 ,      
  cs_catalog_page_sk int4 ,     
  cs_ship_mode_sk int4 ,        
  cs_warehouse_sk int4 ,        
  cs_item_sk int4  ,    
  cs_promo_sk int4 ,            
  cs_order_number int8  ,                 
  cs_quantity int4 ,            
  cs_wholesale_cost numeric(7,2) ,                
  cs_list_price numeric(7,2) ,  
  cs_sales_price numeric(7,2) , 
  cs_ext_discount_amt numeric(7,2) ,              
  cs_ext_sales_price numeric(7,2) ,               
  cs_ext_wholesale_cost numeric(7,2) ,            
  cs_ext_list_price numeric(7,2) ,
  cs_ext_tax numeric(7,2) ,     
  cs_coupon_amt numeric(7,2) , 
  cs_ext_ship_cost numeric(7,2) ,                
  cs_net_paid numeric(7,2) ,   
  cs_net_paid_inc_tax numeric(7,2) ,             
  cs_net_paid_inc_ship numeric(7,2) ,            
  cs_net_paid_inc_ship_tax numeric(7,2) ,        
  cs_net_profit numeric(7,2)
)
row format delimited
fields terminated by '|'
stored as textfile
LOCATION 's3://redshift-downloads/TPC-DS/2.13/3TB/catalog_sales/';



CREATE EXTERNAL TABLE ext_tpcds_3t.store_sales
(
ss_sold_date_sk int4 ,
  ss_sold_time_sk int4 , 
  ss_item_sk int4  ,  
  ss_customer_sk int4 ,   
  ss_cdemo_sk int4 ,  
  ss_hdemo_sk int4 , 
  ss_addr_sk int4 ,   
  ss_store_sk int4 ,   
  ss_promo_sk int4 ,   
  ss_ticket_number int8 ,
  ss_quantity int4 ,   
  ss_wholesale_cost numeric(7,2) ,  
  ss_list_price numeric(7,2) ,  
  ss_sales_price numeric(7,2) ,
  ss_ext_discount_amt numeric(7,2) , 
  ss_ext_sales_price numeric(7,2) ,  
  ss_ext_wholesale_cost numeric(7,2) ,   
  ss_ext_list_price numeric(7,2) ,   
  ss_ext_tax numeric(7,2) , 
  ss_coupon_amt numeric(7,2) , 
  ss_net_paid numeric(7,2) ,   
  ss_net_paid_inc_tax numeric(7,2) , 
  ss_net_profit numeric(7,2)
)
row format delimited
fields terminated by '|'
stored as textfile
LOCATION 's3://redshift-downloads/TPC-DS/2.13/3TB/store_sales/';



CREATE EXTERNAL TABLE ext_tpcds_3t.store_returns
(
sr_returned_date_sk int4 ,
  sr_return_time_sk int4 ,
  sr_item_sk int4  ,  
  sr_customer_sk int4 ,   
  sr_cdemo_sk int4 ,  
  sr_hdemo_sk int4 ,  
  sr_addr_sk int4 ,   
  sr_store_sk int4 ,  
  sr_reason_sk int4 , 
  sr_ticket_number int8 ,   
  sr_return_quantity int4 ,   
  sr_return_amt numeric(7,2) ,
  sr_return_tax numeric(7,2) ,
  sr_return_amt_inc_tax numeric(7,2) ,  
  sr_fee numeric(7,2) ,   
  sr_return_ship_cost numeric(7,2) ,
  sr_refunded_cash numeric(7,2) ,   
  sr_reversed_charge numeric(7,2) , 
  sr_store_credit numeric(7,2) ,
  sr_net_loss numeric(7,2)
)
row format delimited
fields terminated by '|'
stored as textfile
LOCATION 's3://redshift-downloads/TPC-DS/2.13/3TB/store_returns/';



CREATE EXTERNAL TABLE ext_tpcds_3t.catalog_returns
(
 cr_returned_date_sk int4 ,  
  cr_returned_time_sk int4 , 
  cr_item_sk int4  , 
  cr_refunded_customer_sk int4 ,
  cr_refunded_cdemo_sk int4 ,   
  cr_refunded_hdemo_sk int4 ,   
  cr_refunded_addr_sk int4 ,
  cr_returning_customer_sk int4 ,
  cr_returning_cdemo_sk int4 ,   
  cr_returning_hdemo_sk int4 ,  
  cr_returning_addr_sk int4 ,   
  cr_call_center_sk int4 ,  
  cr_catalog_page_sk int4 , 
  cr_ship_mode_sk int4 ,
  cr_warehouse_sk int4 ,
  cr_reason_sk int4 ,   
  cr_order_number int8 ,
  cr_return_quantity int4 , 
  cr_return_amount numeric(7,2) ,
  cr_return_tax numeric(7,2) ,   
  cr_return_amt_inc_tax numeric(7,2) ,
  cr_fee numeric(7,2) , 
  cr_return_ship_cost numeric(7,2) , 
  cr_refunded_cash numeric(7,2) ,
  cr_reversed_charge numeric(7,2) ,  
  cr_store_credit numeric(7,2) ,
  cr_net_loss numeric(7,2)
)
row format delimited
fields terminated by '|'
stored as textfile
LOCATION 's3://redshift-downloads/TPC-DS/2.13/3TB/catalog_returns/';
;

CREATE EXTERNAL TABLE ext_tpcds_3t.web_returns
(
wr_returned_date_sk int4 ,   
  wr_returned_time_sk int4 , 
  wr_item_sk int4  , 
  wr_refunded_customer_sk int4 ,
  wr_refunded_cdemo_sk int4 ,   
  wr_refunded_hdemo_sk int4 ,   
  wr_refunded_addr_sk int4 ,
  wr_returning_customer_sk int4 ,
  wr_returning_cdemo_sk int4 ,   
  wr_returning_hdemo_sk int4 ,  
  wr_returning_addr_sk int4 ,   
  wr_web_page_sk int4 , 
  wr_reason_sk int4 ,   
  wr_order_number int8 ,
  wr_return_quantity int4 , 
  wr_return_amt numeric(7,2) ,  
  wr_return_tax numeric(7,2) ,  
  wr_return_amt_inc_tax numeric(7,2) ,
  wr_fee numeric(7,2) , 
  wr_return_ship_cost numeric(7,2) ,
  wr_refunded_cash numeric(7,2) ,   
  wr_reversed_charge numeric(7,2) ,  
  wr_account_credit numeric(7,2) ,   
  wr_net_loss numeric(7,2)
)
row format delimited
fields terminated by '|'
stored as textfile
LOCATION 's3://redshift-downloads/TPC-DS/2.13/3TB/web_returns/';

Please run following query scanning S3 datasets. 

NOTE: For the very first run of this query, the data warehouse will not have history of the query statistics. So, you may need to run this query twice for scaling algorithms to make scaling decisions. Please re-run if the query did not scale on the very first run

In [0]:
-- Run below spectrum query scanning S3 datasets.  It may run for ~10minutes.
SET enable_result_cache_for_session TO off;
with /* TPC-DS demo data lake query */
	ws as
	(select d_year AS ws_sold_year, ws_item_sk,    ws_bill_customer_sk
     ws_customer_sk,    sum(ws_quantity) ws_qty,    sum(ws_wholesale_cost) ws_wc,
        sum(ws_sales_price) ws_sp   from ext_tpcds_3t.web_sales   left join ext_tpcds_3t.web_returns on
     wr_order_number=ws_order_number and ws_item_sk=wr_item_sk   join ext_tpcds_3t.date_dim
     on ws_sold_date_sk = d_date_sk   where wr_order_number is null   group by
     d_year, ws_item_sk, ws_bill_customer_sk   ),
	cs as  
	(select d_year AS cs_sold_year,
     cs_item_sk,    cs_bill_customer_sk cs_customer_sk,    sum(cs_quantity) cs_qty,
        sum(cs_wholesale_cost) cs_wc,    sum(cs_sales_price) cs_sp   from ext_tpcds_3t.catalog_sales
       left join ext_tpcds_3t.catalog_returns on cr_order_number=cs_order_number and cs_item_sk=cr_item_sk
       join ext_tpcds_3t.date_dim on cs_sold_date_sk = d_date_sk   where cr_order_number is
     null   group by d_year, cs_item_sk, cs_bill_customer_sk   ),
	ss as  
	(select
     d_year AS ss_sold_year, ss_item_sk,    ss_customer_sk,    sum(ss_quantity)
     ss_qty,    sum(ss_wholesale_cost) ss_wc,    sum(ss_sales_price) ss_sp
       from ext_tpcds_3t.store_sales left join ext_tpcds_3t.store_returns on sr_ticket_number=ss_ticket_number
     and ss_item_sk=sr_item_sk   join ext_tpcds_3t.date_dim on ss_sold_date_sk = d_date_sk
       where sr_ticket_number is null   group by d_year, ss_item_sk, ss_customer_sk
       ) 
	   
	   select 
	   ss_customer_sk,round(ss_qty/(coalesce(ws_qty+cs_qty,1)),2)
     ratio,ss_qty store_qty, ss_wc store_wholesale_cost, ss_sp store_sales_price,
    coalesce(ws_qty,0)+coalesce(cs_qty,0) other_chan_qty,coalesce(ws_wc,0)+coalesce(cs_wc,0)
     other_chan_wholesale_cost,coalesce(ws_sp,0)+coalesce(cs_sp,0) other_chan_sales_price
    from ss left join ws on (ws_sold_year=ss_sold_year and ws_item_sk=ss_item_sk
     and ws_customer_sk=ss_customer_sk)left join cs on (cs_sold_year=ss_sold_year
     and cs_item_sk=cs_item_sk and cs_customer_sk=ss_customer_sk)where coalesce(ws_qty,0)>0
     and coalesce(cs_qty, 0)>0 order by   ss_customer_sk,  ss_qty desc, ss_wc
     desc, ss_sp desc,  other_chan_qty,  other_chan_wholesale_cost,  other_chan_sales_price,
      round(ss_qty/(coalesce(ws_qty+cs_qty,1)),2)

In [0]:
-- Review total elapsed time of the query.  You need the start_time and end_time from the results to feed into next query.
select query_id,query_text,start_time,end_time, elapsed_time/1000000.0 duration_in_seconds 
from sys_query_history 
where query_text like '%TPC-DS demo data lake query%'
and query_text not like '%sys_query_history%'
order by start_time desc

In [0]:
-- Observe the compute scaled during the above start_time and end_time period.  Replace start_time and end_time in below query from output of the above query.  
select * from sys_serverless_usage
where end_time >= '2024-06-03 16:53:56.126926' 
and end_time <= DATEADD(minute,1,'2024-06-03 16:56:14.612149') 
order by end_time asc
 
-- You can notice the increased compute_capacity for this spectrum query.

## Cleanup

1. Delete Redshift Serverless workgroup. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless_delete-workgroup.html) for documentation to delete workgroup.
2. Delete Redshift Serverelss associated namespace. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-console-namespace-delete.html) for documentation to delete workgroup.